In [9]:
### 크롤링 한번에 모으기

# 패키지 불러오기
import pandas as pd
from selenium import webdriver
import time
from selenium.webdriver import ActionChains
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.keys import Keys
from openpyxl import Workbook
import datetime

# 인당 80종류의 음식을 들고옴(자기거 빼고 주석처리!)
# 80개는 터져서 10개씩 나눠서 진행하길 권장
df = pd.read_excel("./음식분류 AI 데이터 영양DB.xlsx")
# df = df.loc[0:79, :]      # 의준
# df = df.loc[120:129, :]    # 민영
# df = df.loc[160:239, :]   # 지아
# df = df.loc[290:299, :]   # 수지
# df = df.loc[385:399, :]   # 지수
df = df.loc[390:399, :] # 노가다

# df에 열 추가하기
df["review"]=[0]*10
df["recipe_title"]=[0]*10
df["ingredient"]=[0]*10

### 검색결과가 없을때 실험용, 나중엔 주석처리하기
# df = df.loc[[398,399]]
# df["review"]=[0]*2
# df["recipe_title"]=[0]*2
# df["hashtag"]=[0]*2
# df["ingredient"]=[0]*2

# 400종류를 나누기로 해서 위처럼 80으로 수정했음
# df["review"]=[0]*400
# df["recipe_title"]=[0]*400
# df["hashtag"]=[0]*400
# df["ingredient"]=[0]*400

# 문자형으로 변형(혹시 몰라서 근데 여기서는 없어도 될듯..?)
# 셀에 하나씩 접근할때 자료형에 따라 함수 처리가 다를 수 있어서
df['review'] = df['review'].astype(str)
df['recipe_title'] = df['recipe_title'].astype(str)
df['ingredient'] = df['ingredient'].astype(str)

# 드라이버 버전 변경할 사람 109 --> 111.0.5563.64
file_path = "c:/ChromeDriver_exe/chrome_112.0.5615.49_driver.exe"
driver = webdriver.Chrome(file_path)

url = "https://www.10000recipe.com/recipe/list.html"
driver.get(url)

# df데이터프레임 
for idx,menu in enumerate(df["음 식 명"]):
    # 검색창에서 해당하는 메뉴 검색하기
    # "김밥" 부분을 엑셀에서 가져와서 자동으로 크롤링할 수 있겠다.
    
    final_title=[]
    final_review=[]
    final_ingredient=[]
    
    time.sleep(3)
    
    input_text = driver.find_element(by=By.ID, value="srhRecipeText")
    input_text.clear()
    input_text.send_keys("{}".format(menu))
    input_text.send_keys(Keys.ENTER)

    time.sleep(3)

    # li 태그엔 40개까지 1부터 40까지 보여준다.
    # 구글 광고 뜰땐 try except
    # 광고 처음에만 뜨니까 driver실행하고 광고 한번 없애고 진행하기
    
    # recipe_num의 검색결과가 없을 때 다음 레시피로 넘어감
    try:
        recipe_num = driver.find_element(by=By.XPATH, value='//*[@id="contents_area_full"]/ul/div/b')
    except:
        continue
    # 콤마때메 오류나던 부분 해결
    recipe_num = int(recipe_num.text.replace(",",""))
    
    # 실험용으로 recipe_num을 3으로 고정
    print(recipe_num)
    
    if recipe_num < 40 :
        recipe_num = recipe_num

    else :
        recipe_num = 40
    for index in range(1,recipe_num,1):
        time.sleep(2)
        
        find_image = driver.find_element(By.XPATH,"/html/body/dl/dd/ul/ul/li[{}]".format(index))
        find_image.click()

        time.sleep(3)
        
        try:

            # 재료 가져와서 리스트에 넣기
            find_ingre = driver.find_element(by=By.CLASS_NAME, value="ready_ingre3")

            ingredient_list=[]
            find_ingre_1 = find_ingre.find_elements(By.XPATH,"ul[*]/li[*]/a[1]")
            for i in find_ingre_1:
                ingredient_list.append(i.text)

            final_ingredient.append(ingredient_list)
        
        except:
            ingredient_list=[]
            final_ingredient.append(ingredient_list)

        # 제목 가져오기
        find_title = driver.find_element(by=By.ID, value="contents_area")
        find_title_real = find_title.find_element(by=By.XPATH, value = "div[2]/h3")
        recipe_title = find_title_real.text
        
        final_title.append([recipe_title])
        
        # 후기 싹 다 가져오기
        # 먼저 후기 전체보기 버튼을 누르자
        # 후기 전체보기 버튼이 없다면 except로
        try:
            find_review_button = driver.find_element(By.XPATH,'//*[@id="btnMoreReviews"]')
            find_review_button.send_keys(Keys.RETURN)

            reviews = []
            find_review = driver.find_elements(By.XPATH,'//div[@class="view_reply st2"]/div[2]/div[*]/div/div[2]/p')
            for i in find_review:
                reviews.append(i.text)
            driver.get("https://www.10000recipe.com/recipe/list.html?q={}".format(menu))
            final_review.append(reviews)
            time.sleep(3)
        # 후기 전체보기 버튼이 없다면 다음 try문으로 간다    
        except:
            # review를 찾아보자. review가 없다면 다음 except문으로
            try:
                reviews=[]
                find_review = driver.find_elements(By.XPATH,'//div[@class="view_reply st2"]/div[2]/div[*]/div/div[2]/p')
                for i in find_review:
                    reviews.append(i.text)
                final_review.append(reviews)
                driver.get("https://www.10000recipe.com/recipe/list.html?q={}".format(menu))
            # review가 없다면 review에 리뷰없음이라는 문구를 추가    
            except:
                reviews=[]
                final_review.append(reviews)
            
            driver.get("https://www.10000recipe.com/recipe/list.html?q={}".format(menu))
            time.sleep(3)

        print("레시피 제목 : ",final_title)
        print("재료 목록 : ",final_ingredient)
        print("리뷰 목록 : ",final_review)
        
    
    # df 저장하기  loc[idx] ---> iloc[idx]     .reset_index(drop=True) 안해도됨!
    df.loc[:,"review"].iloc[idx]=final_review
    df.loc[:,"recipe_title"].iloc[idx]=[final_title]
    df.loc[:,"ingredient"].iloc[idx]=[final_ingredient]
    

driver.quit()

# 저장명은 ?~??_food.csv로 통일 
# df.to_excel("./100_food.xlsx")
df.to_csv("./390_399_food.csv")

# 확인용 프린트
print("레시피 제목 : ",recipe_title)
print("재료 목록 : ",ingredient_list)
print("리뷰 목록 : ",reviews)

C:\Users\Administrator\AppData\Local\Temp\ipykernel_18156\2768430609.py:51: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(file_path)


222
레시피 제목 :  [['남은 현미밥으로 인절미 만들기']]
재료 목록 :  [['현미밥', '콩가루', '소금', '참기름', '설탕']]
리뷰 목록 :  [['찰밥 해먹고 남은걸로해봤는데 정말 맛있었어요~^^ ', '따라하기 쉬운방법이네요 ']]
레시피 제목 :  [['남은 현미밥으로 인절미 만들기'], ['초등학생도 간편하게! 어버이날 인절미 만들기!']]
재료 목록 :  [['현미밥', '콩가루', '소금', '참기름', '설탕'], ['찹쌀가루', '따뜻한 물', '설탕', '소금', '콩가루']]
리뷰 목록 :  [['찰밥 해먹고 남은걸로해봤는데 정말 맛있었어요~^^ ', '따라하기 쉬운방법이네요 '], ['쉽게 만들 수 있어서 너무 좋아요 ']]
레시피 제목 :  [['남은 현미밥으로 인절미 만들기'], ['초등학생도 간편하게! 어버이날 인절미 만들기!'], ['#봄제철재료 #쑥요리 #쑥개떡만들기 #쑥인절미만들기 #찹쌀가루만들기 #콩가루 #봄재철쑥']]
재료 목록 :  [['현미밥', '콩가루', '소금', '참기름', '설탕'], ['찹쌀가루', '따뜻한 물', '설탕', '소금', '콩가루'], ['찹쌀', '쑥', '쌀가루', '쑥가루', '소금', '콩가루', '참기름']]
리뷰 목록 :  [['찰밥 해먹고 남은걸로해봤는데 정말 맛있었어요~^^ ', '따라하기 쉬운방법이네요 '], ['쉽게 만들 수 있어서 너무 좋아요 '], []]
레시피 제목 :  [['남은 현미밥으로 인절미 만들기'], ['초등학생도 간편하게! 어버이날 인절미 만들기!'], ['#봄제철재료 #쑥요리 #쑥개떡만들기 #쑥인절미만들기 #찹쌀가루만들기 #콩가루 #봄재철쑥'], ['#봄제철재료 #쑥요리 #쑥개떡만들기 #쑥인절미만들기 #찹쌀가루만들기 #콩가루 #봄재철쑥']]
재료 목록 :  [['현미밥', '콩가루', '소금', '참기름', '설탕'], ['찹쌀가루', '따뜻한 물', '설탕', '소금', '콩가루'], ['찹쌀', '쑥', '쌀가루', '쑥가루', '소금',

C:\Users\Administrator\AppData\Local\Temp\ipykernel_18156\2768430609.py:163: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[:,"review"].iloc[idx]=final_review
C:\Users\Administrator\AppData\Local\Temp\ipykernel_18156\2768430609.py:164: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[:,"recipe_title"].iloc[idx]=[final_title]
C:\Users\Administrator\AppData\Local\Temp\ipykernel_18156\2768430609.py:165: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-

26
레시피 제목 :  [['앙꼬절편(앙금떡) 만들기']]
재료 목록 :  [['물', '앙금']]
리뷰 목록 :  [[]]
레시피 제목 :  [['앙꼬절편(앙금떡) 만들기'], ['알록달록 절편']]
재료 목록 :  [['물', '앙금'], ['멥쌀가루(방앗간에서 빻아온것)', '물', '백련초가루', '쑥가루', '호박가루', '참기름', '식용유', '소금']]
리뷰 목록 :  [[], []]
레시피 제목 :  [['앙꼬절편(앙금떡) 만들기'], ['알록달록 절편'], ['지팡이절편/떡 만들기']]
재료 목록 :  [['물', '앙금'], ['멥쌀가루(방앗간에서 빻아온것)', '물', '백련초가루', '쑥가루', '호박가루', '참기름', '식용유', '소금'], ['멥쌀가루', '물', '소금', '말차가루', '백련초가루', '참기름', '기름']]
리뷰 목록 :  [[], [], []]
레시피 제목 :  [['앙꼬절편(앙금떡) 만들기'], ['알록달록 절편'], ['지팡이절편/떡 만들기'], ['생강청과 생강절편']]
재료 목록 :  [['물', '앙금'], ['멥쌀가루(방앗간에서 빻아온것)', '물', '백련초가루', '쑥가루', '호박가루', '참기름', '식용유', '소금'], ['멥쌀가루', '물', '소금', '말차가루', '백련초가루', '참기름', '기름'], ['생강', '설탕']]
리뷰 목록 :  [[], [], [], ['500g만들었는데 1주일만에 거의 바닥을 보이네요~~ 감사합니다 ', '너무 맛있게 만들었답니 ', '맛있어요. 저는 생강을 물에 쫌 오래 담궈서 덜맵게해서~ . 설탕 덜 넣었는데 도 맛나네요~ 정말~~정성 가득 !!건강 간식이네요 ', '쉽고 빠르게 할 수 있어서 좋습니다 ', '저도 황설탕으로 했어요 ', '황설탕을 넣어서 ㅠㅠ ']]
레시피 제목 :  [['앙꼬절편(앙금떡) 만들기'], ['알록달록 절편'], ['지팡이절편/떡 만들기'], ['생강청과 생강절편'], ['냉동실 절편으로 만든 떡복기']]
재료 